In [1]:
from datetime import datetime
import pandas as pd
import numpy as np
from dateutil.relativedelta import relativedelta
import plotly as py
from plotly import graph_objs as go
import plotly.express as px
import matplotlib.pyplot as plt
from matplotlib.ticker import StrMethodFormatter

In [33]:
data = pd.read_csv('2024-01-29_dhs_gisaid_merge_LD.csv')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22643 entries, 0 to 22642
Data columns (total 68 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Unnamed: 0                       22643 non-null  int64  
 1   GISAID_Name                      22643 non-null  object 
 2   SampleID                         22643 non-null  object 
 3   WEDSS_DOC                        22643 non-null  object 
 4   WSLH_DOC                         7757 non-null   object 
 5   MHDL_DOC                         5532 non-null   object 
 6   CDC_DOC                          455 non-null    object 
 7   AVRL_DOC                         8899 non-null   object 
 8   ClientID                         22643 non-null  int64  
 9   Age                              22643 non-null  int64  
 10  Gender.x                         22627 non-null  object 
 11  Race                             22611 non-null  object 
 12  Ethnicity         

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/1343519819.py:1: DtypeWarning:

Columns (4,5,6,7,13,28,29,37,38,39,40,41,42,43,44,45,46,47,48,49,50,55,60,62) have mixed types. Specify dtype option on import or set low_memory=False.



In [34]:
#some dupe entries =, ~200ish
data = data.drop_duplicates(subset=['SampleID', 'ClientID'])
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 22526 entries, 0 to 22642
Data columns (total 68 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Unnamed: 0                       22526 non-null  int64  
 1   GISAID_Name                      22526 non-null  object 
 2   SampleID                         22526 non-null  object 
 3   WEDSS_DOC                        22526 non-null  object 
 4   WSLH_DOC                         7731 non-null   object 
 5   MHDL_DOC                         5526 non-null   object 
 6   CDC_DOC                          455 non-null    object 
 7   AVRL_DOC                         8814 non-null   object 
 8   ClientID                         22526 non-null  int64  
 9   Age                              22526 non-null  int64  
 10  Gender.x                         22510 non-null  object 
 11  Race                             22494 non-null  object 
 12  Ethnicity              

In [35]:

# Convert multiple date columns to datetime objects
date_cols = ['WEDSS_DOC', 'VacDate1', 'VacDate2', 'VacDate3','VacDate4','VacDate5','VacDate6']
data[date_cols] = data[date_cols].apply(pd.to_datetime, errors='coerce')

# Format date columns in specific format '%Y-%m-%d'
data[date_cols] = data[date_cols].apply(lambda x: x.dt.strftime('%Y-%m-%d'))

sub_data =(data[date_cols])
sub_data
#temp_df.info()

WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5  \
0      2021-07-27         NaN         NaN         NaN      NaN      NaN   
1      2021-08-06         NaN         NaN         NaN      NaN      NaN   
2      2021-11-12         NaN         NaN         NaN      NaN      NaN   
3      2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN   
4      2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN   
...           ...         ...         ...         ...      ...      ...   
22638  2021-12-26         NaN         NaN         NaN      NaN      NaN   
22639  2021-12-24  2021-03-15         NaN         NaN      NaN      NaN   
22640  2021-12-23  2021-02-11  2021-03-04  2021-10-09      NaN      NaN   
22641  2021-12-24         NaN         NaN         NaN      NaN      NaN   
22642  2021-12-25  2021-01-28  2021-02-26         NaN      NaN      NaN   

      VacDate6  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  
...        ...  
22638      NaN  
22639      NaN  
22640      NaN  
22641      NaN  
22642      NaN  

[22526 rows x 7 columns]

In [36]:
#loop to remove irrelevant vax dates that are after sample (vaxdates that are after WEDSS_DOC)
for col in date_cols[1:]:
    sub_data.loc[sub_data['WEDSS_DOC'] < sub_data[col], col] = pd.NaT

sub_data
#temp_df.head(50)
#temp_df['VacDate4'].unique()

WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5  \
0      2021-07-27         NaN         NaN         NaN      NaN      NaN   
1      2021-08-06         NaN         NaN         NaN      NaN      NaN   
2      2021-11-12         NaN         NaN         NaN      NaN      NaN   
3      2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN   
4      2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN   
...           ...         ...         ...         ...      ...      ...   
22638  2021-12-26         NaN         NaN         NaN      NaN      NaN   
22639  2021-12-24  2021-03-15         NaN         NaN      NaN      NaN   
22640  2021-12-23  2021-02-11  2021-03-04  2021-10-09      NaN      NaN   
22641  2021-12-24         NaN         NaN         NaN      NaN      NaN   
22642  2021-12-25  2021-01-28  2021-02-26         NaN      NaN      NaN   

      VacDate6  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  
...        ...  
22638      NaN  
22639      NaN  
22640      NaN  
22641      NaN  
22642      NaN  

[22526 rows x 7 columns]

In [37]:
#find most recent date in each row and put it in a new column "most_recent"
for index, row in sub_data.iterrows():
    valid_dates = [date for date in row[1:] if not (pd.isnull(date) or date == pd.NaT)]
    if valid_dates:
        sub_data.loc[index, 'most_recent'] = max(valid_dates)
    else:
        sub_data.loc[index, 'most_recent'] = np.nan

sub_data.head(50)
#temp_df.head(25)

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/4044477574.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5 VacDate6  \
0   2021-07-27         NaN         NaN         NaN      NaN      NaN      NaN   
1   2021-08-06         NaN         NaN         NaN      NaN      NaN      NaN   
2   2021-11-12         NaN         NaN         NaN      NaN      NaN      NaN   
3   2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
4   2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
5   2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
6   2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
7   2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
8   2021-11-26  2021-03-14  2021-04-15         NaN      NaN      NaN      NaN   
9   2021-11-26  2021-01-23  2021-02-20  2021-11-18      NaN      NaN      NaN   
10  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
11  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
12  2021-11-26  2021-02-24  2021-03-24         NaN      NaN      NaN      NaN   
13  2021-11-26  2021-01-23  2021-02-20         NaT      NaN      NaN      NaN   
14  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
15  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
16  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
17  2021-11-26  2021-01-29  2021-02-26         NaN      NaN      NaN      NaN   
18  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
19  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
20  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
21  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
22  2021-11-26  2021-03-30  2021-04-20  2021-09-10      NaN      NaN      NaN   
23  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
24  2021-11-26  2021-05-19  2021-06-09         NaN      NaN      NaN      NaN   
25  2021-11-27         NaN         NaN         NaN      NaN      NaN      NaN   
26  2021-11-27         NaN         NaN         NaN      NaN      NaN      NaN   
27  2021-12-11         NaN         NaN         NaN      NaN      NaN      NaN   
28  2021-12-11         NaN         NaN         NaN      NaN      NaN      NaN   
29  2021-12-14         NaN         NaN         NaN      NaN      NaN      NaN   
30  2021-12-15  2021-01-04  2021-02-01         NaN      NaN      NaN      NaN   
31  2021-12-17         NaN         NaN         NaN      NaN      NaN      NaN   
32  2021-12-17  2021-04-06  2021-04-27         NaN      NaN      NaN      NaN   
33  2021-12-17         NaN         NaN         NaN      NaN      NaN      NaN   
34  2021-12-21         NaN         NaN         NaN      NaN      NaN      NaN   
35  2021-12-24         NaN         NaN         NaN      NaN      NaN      NaN   
36  2021-12-28         NaN         NaN         NaN      NaN      NaN      NaN   
37  2022-01-15         NaN         NaN         NaN      NaN      NaN      NaN   
38  2022-01-17         NaN         NaN         NaN      NaN      NaN      NaN   
39  2022-01-18         NaN         NaN         NaN      NaN      NaN      NaN   
40  2022-01-18         NaN         NaN         NaN      NaN      NaN      NaN   
41  2022-01-18         NaN         NaN         NaN      NaN      NaN      NaN   
42  2022-01-18         NaN         NaN         NaN      NaN      NaN      NaN   
43  2022-01-19         NaN         NaN         NaN      NaN      NaN      NaN   
44  2022-01-20         NaN         NaN         NaN      NaN      NaN      NaN   
45  2022-01-23  2021-04-07  2021-05-05         NaN      NaN      NaN      NaN   
46  2022-01-23         NaN         NaN         NaN      NaN      NaN      NaN   
47  2022-01-23  2021-03-12  2021-04-09         NaN      NaN      NaN      NaN   
48  2022-01-23  2021-08-24  2021-09-

In [38]:
#now making a comparison function, first have to deal with NaN values, then do comparison for actual dates
#combine years and months comparisons to get total in months, apply this result to new 'diff' column

sub_data['WEDSS_DOC'] = pd.to_datetime(sub_data['WEDSS_DOC'])
sub_data['most_recent'] = pd.to_datetime(sub_data['most_recent'])

# Calculate the difference in months between 'start' and 'end' and store it in a new column 'res'
def calculate_month_difference(row):
    if pd.isnull(row['WEDSS_DOC']) or pd.isnull(row['most_recent']):
        return np.nan
    else:
        return (row['WEDSS_DOC'].year - row['most_recent'].year) * 12 + (row['WEDSS_DOC'].month - row['most_recent'].month)

sub_data['diff'] = sub_data.apply(calculate_month_difference, axis=1)

sub_data.head(25)
#temp_df.head(25)

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/4160042591.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/4160042591.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/4160042591.py:14: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the 

WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5 VacDate6  \
0  2021-07-27         NaN         NaN         NaN      NaN      NaN      NaN   
1  2021-08-06         NaN         NaN         NaN      NaN      NaN      NaN   
2  2021-11-12         NaN         NaN         NaN      NaN      NaN      NaN   
3  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
4  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
5  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
6  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
7  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
8  2021-11-26  2021-03-14  2021-04-15         NaN      NaN      NaN      NaN   
9  2021-11-26  2021-01-23  2021-02-20  2021-11-18      NaN      NaN      NaN   
10 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
11 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
12 2021-11-26  2021-02-24  2021-03-24         NaN      NaN      NaN      NaN   
13 2021-11-26  2021-01-23  2021-02-20         NaT      NaN      NaN      NaN   
14 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
15 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
16 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
17 2021-11-26  2021-01-29  2021-02-26         NaN      NaN      NaN      NaN   
18 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
19 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
20 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
21 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
22 2021-11-26  2021-03-30  2021-04-20  2021-09-10      NaN      NaN      NaN   
23 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
24 2021-11-26  2021-05-19  2021-06-09         NaN      NaN      NaN      NaN   

   most_recent  diff  
0          NaT   NaN  
1          NaT   NaN  
2          NaT   NaN  
3   2021-02-20   9.0  
4   2021-02-20   9.0  
5          NaT   NaN  
6          NaT   NaN  
7          NaT   NaN  
8   2021-04-15   7.0  
9   2021-11-18   0.0  
10         NaT   NaN  
11         NaT   NaN  
12  2021-03-24   8.0  
13  2021-02-20   9.0  
14         NaT   NaN  
15         NaT   NaN  
16         NaT   NaN  
17  2021-02-26   9.0  
18         NaT   NaN  
19  2021-02-20   9.0  
20  2021-02-20   9.0  
21         NaT   NaN  
22  2021-09-10   2.0  
23         NaT   NaN  
24  2021-06-09   5.0

In [39]:
#now deteriming if more than 6mos since most recent vax and adding that result to new column

sub_data['more_than_6mos'] = np.where(sub_data['diff'] > 6, True,
                                     np.where(sub_data['diff'] <= 6, False, np.nan))
sub_data.head(25)
#temp_df.head(25)

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/3105999824.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5 VacDate6  \
0  2021-07-27         NaN         NaN         NaN      NaN      NaN      NaN   
1  2021-08-06         NaN         NaN         NaN      NaN      NaN      NaN   
2  2021-11-12         NaN         NaN         NaN      NaN      NaN      NaN   
3  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
4  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
5  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
6  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
7  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
8  2021-11-26  2021-03-14  2021-04-15         NaN      NaN      NaN      NaN   
9  2021-11-26  2021-01-23  2021-02-20  2021-11-18      NaN      NaN      NaN   
10 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
11 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
12 2021-11-26  2021-02-24  2021-03-24         NaN      NaN      NaN      NaN   
13 2021-11-26  2021-01-23  2021-02-20         NaT      NaN      NaN      NaN   
14 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
15 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
16 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
17 2021-11-26  2021-01-29  2021-02-26         NaN      NaN      NaN      NaN   
18 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
19 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
20 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
21 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
22 2021-11-26  2021-03-30  2021-04-20  2021-09-10      NaN      NaN      NaN   
23 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
24 2021-11-26  2021-05-19  2021-06-09         NaN      NaN      NaN      NaN   

   most_recent  diff  more_than_6mos  
0          NaT   NaN             NaN  
1          NaT   NaN             NaN  
2          NaT   NaN             NaN  
3   2021-02-20   9.0             1.0  
4   2021-02-20   9.0             1.0  
5          NaT   NaN             NaN  
6          NaT   NaN             NaN  
7          NaT   NaN             NaN  
8   2021-04-15   7.0             1.0  
9   2021-11-18   0.0             0.0  
10         NaT   NaN             NaN  
11         NaT   NaN             NaN  
12  2021-03-24   8.0             1.0  
13  2021-02-20   9.0             1.0  
14         NaT   NaN             NaN  
15         NaT   NaN             NaN  
16         NaT   NaN             NaN  
17  2021-02-26   9.0             1.0  
18         NaT   NaN             NaN  
19  2021-02-20   9.0             1.0  
20  2021-02-20   9.0             1.0  
21         NaT   NaN             NaN  
22  2021-09-10   2.0             0.0  
23         NaT   NaN             NaN  
24  2021-06-09   5.0             0.0

In [40]:
#creating a column for count of # of vaccinations

vax_cols = [1, 2, 3, 4, 5, 6]  #column index positions

# Calculate the count of non-null values across specific columns by index positions and store the sum in a new 'count' column
sub_data['vax_count'] = sub_data.iloc[:, vax_cols].count(axis=1)

sub_data.head(25)
#temp_df.head(50)

/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/2778117363.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5 VacDate6  \
0  2021-07-27         NaN         NaN         NaN      NaN      NaN      NaN   
1  2021-08-06         NaN         NaN         NaN      NaN      NaN      NaN   
2  2021-11-12         NaN         NaN         NaN      NaN      NaN      NaN   
3  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
4  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
5  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
6  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
7  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
8  2021-11-26  2021-03-14  2021-04-15         NaN      NaN      NaN      NaN   
9  2021-11-26  2021-01-23  2021-02-20  2021-11-18      NaN      NaN      NaN   
10 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
11 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
12 2021-11-26  2021-02-24  2021-03-24         NaN      NaN      NaN      NaN   
13 2021-11-26  2021-01-23  2021-02-20         NaT      NaN      NaN      NaN   
14 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
15 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
16 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
17 2021-11-26  2021-01-29  2021-02-26         NaN      NaN      NaN      NaN   
18 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
19 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
20 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
21 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
22 2021-11-26  2021-03-30  2021-04-20  2021-09-10      NaN      NaN      NaN   
23 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
24 2021-11-26  2021-05-19  2021-06-09         NaN      NaN      NaN      NaN   

   most_recent  diff  more_than_6mos  vax_count  
0          NaT   NaN             NaN          0  
1          NaT   NaN             NaN          0  
2          NaT   NaN             NaN          0  
3   2021-02-20   9.0             1.0          2  
4   2021-02-20   9.0             1.0          2  
5          NaT   NaN             NaN          0  
6          NaT   NaN             NaN          0  
7          NaT   NaN             NaN          0  
8   2021-04-15   7.0             1.0          2  
9   2021-11-18   0.0             0.0          3  
10         NaT   NaN             NaN          0  
11         NaT   NaN             NaN          0  
12  2021-03-24   8.0             1.0          2  
13  2021-02-20   9.0             1.0          2  
14         NaT   NaN             NaN          0  
15         NaT   NaN             NaN          0  
16         NaT   NaN             NaN          0  
17  2021-02-26   9.0             1.0          2  
18         NaT   NaN             NaN          0  
19  2021-02-20   9.0             1.0          2  
20  2021-02-20   9.0             1.0          2  
21         NaT   NaN             NaN          0  
22  2021-09-10   2.0             0.0          3  
23         NaT   NaN             NaN          0  
24  2021-06-09   5.0             0.0          2

In [41]:
counts= sub_data['vax_count'].value_counts()
print(counts)

vax_count
0    14600
2     4008
3     2576
1      841
4      416
5       83
6        2
Name: count, dtype: int64


In [42]:
sub_data['1dose_or_more'] = np.where(sub_data['vax_count'] > 0, True, False)
sub_data.head(25)


/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/3581022453.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



WEDSS_DOC    VacDate1    VacDate2    VacDate3 VacDate4 VacDate5 VacDate6  \
0  2021-07-27         NaN         NaN         NaN      NaN      NaN      NaN   
1  2021-08-06         NaN         NaN         NaN      NaN      NaN      NaN   
2  2021-11-12         NaN         NaN         NaN      NaN      NaN      NaN   
3  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
4  2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
5  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
6  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
7  2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
8  2021-11-26  2021-03-14  2021-04-15         NaN      NaN      NaN      NaN   
9  2021-11-26  2021-01-23  2021-02-20  2021-11-18      NaN      NaN      NaN   
10 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
11 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
12 2021-11-26  2021-02-24  2021-03-24         NaN      NaN      NaN      NaN   
13 2021-11-26  2021-01-23  2021-02-20         NaT      NaN      NaN      NaN   
14 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
15 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
16 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
17 2021-11-26  2021-01-29  2021-02-26         NaN      NaN      NaN      NaN   
18 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
19 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
20 2021-11-26  2021-01-23  2021-02-20         NaN      NaN      NaN      NaN   
21 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
22 2021-11-26  2021-03-30  2021-04-20  2021-09-10      NaN      NaN      NaN   
23 2021-11-26         NaN         NaN         NaN      NaN      NaN      NaN   
24 2021-11-26  2021-05-19  2021-06-09         NaN      NaN      NaN      NaN   

   most_recent  diff  more_than_6mos  vax_count  1dose_or_more  
0          NaT   NaN             NaN          0          False  
1          NaT   NaN             NaN          0          False  
2          NaT   NaN             NaN          0          False  
3   2021-02-20   9.0             1.0          2           True  
4   2021-02-20   9.0             1.0          2           True  
5          NaT   NaN             NaN          0          False  
6          NaT   NaN             NaN          0          False  
7          NaT   NaN             NaN          0          False  
8   2021-04-15   7.0             1.0          2           True  
9   2021-11-18   0.0             0.0          3           True  
10         NaT   NaN             NaN          0          False  
11         NaT   NaN             NaN          0          False  
12  2021-03-24   8.0             1.0          2           True  
13  2021-02-20   9.0             1.0          2           True  
14         NaT   NaN             NaN          0          False  
15         NaT   NaN             NaN          0          False  
16         NaT   NaN             NaN          0          False  
17  2021-02-26   9.0             1.0          2           True  
18         NaT   NaN             NaN          0          False  
19  2021-02-20   9.0             1.0          2           True  
20  2021-02-20   9.0             1.0          2           True  
21         NaT   NaN             NaN          0          False  
22  2021-09-10   2.0             0.0          3           True  
23         NaT   NaN             NaN          0          False  
24  2021-06-09   5.0             0.0          2           True

In [43]:
data1 = pd.merge(data, sub_data[['most_recent','diff','more_than_6mos', 'vax_count', '1dose_or_more']], 
                 left_index=True, right_index=True)

data1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 22526 entries, 0 to 22642
Data columns (total 73 columns):
 #   Column                           Non-Null Count  Dtype         
---  ------                           --------------  -----         
 0   Unnamed: 0                       22526 non-null  int64         
 1   GISAID_Name                      22526 non-null  object        
 2   SampleID                         22526 non-null  object        
 3   WEDSS_DOC                        22526 non-null  object        
 4   WSLH_DOC                         7731 non-null   object        
 5   MHDL_DOC                         5526 non-null   object        
 6   CDC_DOC                          455 non-null    object        
 7   AVRL_DOC                         8814 non-null   object        
 8   ClientID                         22526 non-null  int64         
 9   Age                              22526 non-null  int64         
 10  Gender.x                         22510 non-null  object        

In [44]:
cols = [30, 31, 32, 33, 34 ,35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 64]
data1.drop(data1.columns[cols],axis=1,inplace=True)
data1.info()
data1.head(25)

<class 'pandas.core.frame.DataFrame'>
Index: 22526 entries, 0 to 22642
Data columns (total 53 columns):
 #   Column                           Non-Null Count  Dtype         
---  ------                           --------------  -----         
 0   Unnamed: 0                       22526 non-null  int64         
 1   GISAID_Name                      22526 non-null  object        
 2   SampleID                         22526 non-null  object        
 3   WEDSS_DOC                        22526 non-null  object        
 4   WSLH_DOC                         7731 non-null   object        
 5   MHDL_DOC                         5526 non-null   object        
 6   CDC_DOC                          455 non-null    object        
 7   AVRL_DOC                         8814 non-null   object        
 8   ClientID                         22526 non-null  int64         
 9   Age                              22526 non-null  int64         
 10  Gender.x                         22510 non-null  object        

Unnamed: 0                          GISAID_Name     SampleID   WEDSS_DOC  \
0           18  hCoV-19/USA/WI-CDC-MMB09489547/2021  MMB09489547  2021-07-27   
1           19  hCoV-19/USA/WI-CDC-MMB09621961/2021  MMB09621961  2021-08-06   
2           20  hCoV-19/USA/WI-CDC-MMB11606910/2021  MMB11606910  2021-11-12   
3           21  hCoV-19/USA/WI-CDC-MMB11840790/2021  MMB11840790  2021-11-26   
4           22  hCoV-19/USA/WI-CDC-MMB11841081/2021  MMB11841081  2021-11-26   
5           23  hCoV-19/USA/WI-CDC-MMB11841215/2021  MMB11841215  2021-11-26   
6           24  hCoV-19/USA/WI-CDC-MMB11841256/2021  MMB11841256  2021-11-26   
7           25  hCoV-19/USA/WI-CDC-MMB11841402/2021  MMB11841402  2021-11-26   
8           26  hCoV-19/USA/WI-CDC-MMB11841461/2021  MMB11841461  2021-11-26   
9           27  hCoV-19/USA/WI-CDC-MMB11841604/2021  MMB11841604  2021-11-26   
10          28  hCoV-19/USA/WI-CDC-MMB11841755/2021  MMB11841755  2021-11-26   
11          29  hCoV-19/USA/WI-CDC-MMB11842241/2021  MMB11842241  2021-11-26   
12          30  hCoV-19/USA/WI-CDC-MMB11842293/2021  MMB11842293  2021-11-26   
13          31  hCoV-19/USA/WI-CDC-MMB11842758/2021  MMB11842758  2021-11-26   
14          32  hCoV-19/USA/WI-CDC-MMB11843057/2021  MMB11843057  2021-11-26   
15          33  hCoV-19/USA/WI-CDC-MMB11843194/2021  MMB11843194  2021-11-26   
16          34  hCoV-19/USA/WI-CDC-MMB11843491/2021  MMB11843491  2021-11-26   
17          35  hCoV-19/USA/WI-CDC-MMB11843789/2021  MMB11843789  2021-11-26   
18          36  hCoV-19/USA/WI-CDC-MMB11843893/2021  MMB11843893  2021-11-26   
19          37  hCoV-19/USA/WI-CDC-MMB11844461/2021  MMB11844461  2021-11-26   
20          38  hCoV-19/USA/WI-CDC-MMB11845948/2021  MMB11845948  2021-11-26   
21          39  hCoV-19/USA/WI-CDC-MMB11847173/2021  MMB11847173  2021-11-26   
22          40  hCoV-19/USA/WI-CDC-MMB11847217/2021  MMB11847217  2021-11-26   
23          41  hCoV-19/USA/WI-CDC-MMB11847253/2021  MMB11847253  2021-11-26   
24          42  hCoV-19/USA/WI-CDC-MMB11847332/2021  MMB11847332  2021-11-26   

   WSLH_DOC MHDL_DOC     CDC_DOC AVRL_DOC  ClientID  Age  ...    Specimen  \
0       NaN      NaN  2021-07-27      NaN  21739410   28  ...  Nasal Swab   
1       NaN      NaN  2021-08-06      NaN  12036462   22  ...  Nasal Swab   
2       NaN      NaN  2021-11-12      NaN   9975757   33  ...  Nasal Swab   
3       NaN      NaN  2021-11-26      NaN  25166552   90  ...  Nasal Swab   
4       NaN      NaN  2021-11-26      NaN  25166572   92  ...  Nasal Swab   
5       NaN      NaN  2021-11-26      NaN  25498493   51  ...  Nasal Swab   
6       NaN      NaN  2021-11-26      NaN   4755055   79  ...  Nasal Swab   
7       NaN      NaN  2021-11-26      NaN  25166558   76  ...  Nasal Swab   
8       NaN      NaN  2021-11-26      NaN  18138193   78  ...  Nasal Swab   
9       NaN      NaN  2021-11-26      NaN  25168641   96  ...  Nasal Swab   
10      NaN      NaN  2021-11-26      NaN  39351549   16  ...  Nasal Swab   
11      NaN      NaN  2021-11-26      NaN   2734729   69  ...  Nasal Swab   
12      NaN      NaN  2021-11-26      NaN  27764286   99  ...  Nasal Swab   
13      NaN      NaN  2021-11-26      NaN  10477446   87  ...  Nasal Swab   
14      NaN      NaN  2021-11-26      NaN  20478056   93  ...  Nasal Swab   
15      NaN      NaN  2021-11-26      NaN   3754761   88  ...  Nasal Swab   
16      NaN      NaN  2021-11-26      NaN  30243730   73  ...  Nasal Swab   
17      NaN      NaN  2021-11-26      NaN  35795624   76  ...  Nasal Swab   
18      NaN      NaN  2021-11-26      NaN  10415392   88  ...  Nasal Swab   
19      NaN      NaN  2021-11-26      NaN  23795682   88  ...  Nasal Swab   
20      NaN      NaN  2021-11-26      NaN     61459   59  ...  Nasal Swab   
21      NaN      NaN  2021-11-26      NaN  26259931    9  ...  Nasal Swab   
22      NaN      NaN  2021-11-26      NaN  27954591   45  ...  Nasal Swab   
23      NaN      NaN  2021-11-26      NaN  20982231   13  ...  Nasal Swab  

In [45]:
county = pd.read_csv('county_FIPS.tsv', sep='\t')
data2 = pd.merge(data1, county, how='left', on='CountyFIPS')
data2.head(25)
data2.info()
data2.to_csv('2024-01-30_meta_AJ-columns-added.csv')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22526 entries, 0 to 22525
Data columns (total 54 columns):
 #   Column                           Non-Null Count  Dtype         
---  ------                           --------------  -----         
 0   Unnamed: 0                       22526 non-null  int64         
 1   GISAID_Name                      22526 non-null  object        
 2   SampleID                         22526 non-null  object        
 3   WEDSS_DOC                        22526 non-null  object        
 4   WSLH_DOC                         7731 non-null   object        
 5   MHDL_DOC                         5526 non-null   object        
 6   CDC_DOC                          455 non-null    object        
 7   AVRL_DOC                         8814 non-null   object        
 8   ClientID                         22526 non-null  int64         
 9   Age                              22526 non-null  int64         
 10  Gender.x                         22510 non-null  object   

In [46]:
data_dane = data2[data2['CountyFIPS'] == 55025]
print(len(data_dane))

data_dane.info()
data_dane.head(25)

6263
<class 'pandas.core.frame.DataFrame'>
Index: 6263 entries, 1 to 22491
Data columns (total 54 columns):
 #   Column                           Non-Null Count  Dtype         
---  ------                           --------------  -----         
 0   Unnamed: 0                       6263 non-null   int64         
 1   GISAID_Name                      6263 non-null   object        
 2   SampleID                         6263 non-null   object        
 3   WEDSS_DOC                        6263 non-null   object        
 4   WSLH_DOC                         707 non-null    object        
 5   MHDL_DOC                         409 non-null    object        
 6   CDC_DOC                          131 non-null    object        
 7   AVRL_DOC                         5016 non-null   object        
 8   ClientID                         6263 non-null   int64         
 9   Age                              6263 non-null   int64         
 10  Gender.x                         6261 non-null   object    

Unnamed: 0                          GISAID_Name     SampleID   WEDSS_DOC  \
1           19  hCoV-19/USA/WI-CDC-MMB09621961/2021  MMB09621961  2021-08-06   
10          28  hCoV-19/USA/WI-CDC-MMB11841755/2021  MMB11841755  2021-11-26   
21          39  hCoV-19/USA/WI-CDC-MMB11847173/2021  MMB11847173  2021-11-26   
22          40  hCoV-19/USA/WI-CDC-MMB11847217/2021  MMB11847217  2021-11-26   
23          41  hCoV-19/USA/WI-CDC-MMB11847253/2021  MMB11847253  2021-11-26   
24          42  hCoV-19/USA/WI-CDC-MMB11847332/2021  MMB11847332  2021-11-26   
27          45  hCoV-19/USA/WI-CDC-MMB12113163/2021  MMB12113163  2021-12-11   
28          46  hCoV-19/USA/WI-CDC-MMB12113182/2021  MMB12113182  2021-12-11   
29          47  hCoV-19/USA/WI-CDC-MMB12179847/2021  MMB12179847  2021-12-14   
30          48  hCoV-19/USA/WI-CDC-MMB12196265/2021  MMB12196265  2021-12-15   
31          49  hCoV-19/USA/WI-CDC-MMB12235951/2021  MMB12235951  2021-12-17   
32          50  hCoV-19/USA/WI-CDC-MMB12236092/2021  MMB12236092  2021-12-17   
33          51  hCoV-19/USA/WI-CDC-MMB12237527/2021  MMB12237527  2021-12-17   
36          54  hCoV-19/USA/WI-CDC-MMB12519061/2021  MMB12519061  2021-12-28   
38          56  hCoV-19/USA/WI-CDC-MMB13588323/2022  MMB13588323  2022-01-17   
39          57  hCoV-19/USA/WI-CDC-MMB13598170/2022  MMB13598170  2022-01-18   
40          58  hCoV-19/USA/WI-CDC-MMB13601745/2022  MMB13601745  2022-01-18   
41          59  hCoV-19/USA/WI-CDC-MMB13606288/2022  MMB13606288  2022-01-18   
42          60  hCoV-19/USA/WI-CDC-MMB13610119/2022  MMB13610119  2022-01-18   
43          61  hCoV-19/USA/WI-CDC-MMB13679259/2022  MMB13679259  2022-01-19   
44          62  hCoV-19/USA/WI-CDC-MMB13744153/2022  MMB13744153  2022-01-20   
73          91  hCoV-19/USA/WI-CDC-MMB13953631/2022  MMB13953631  2022-01-27   
75          93  hCoV-19/USA/WI-CDC-MMB13969606/2022  MMB13969606  2022-01-27   
76          94  hCoV-19/USA/WI-CDC-MMB13978740/2022  MMB13978740  2022-01-27   
78          96  hCoV-19/USA/WI-CDC-MMB14021748/2022  MMB14021748  2022-01-30   

   WSLH_DOC MHDL_DOC     CDC_DOC AVRL_DOC  ClientID  Age  ...  \
1       NaN      NaN  2021-08-06      NaN  12036462   22  ...   
10      NaN      NaN  2021-11-26      NaN  39351549   16  ...   
21      NaN      NaN  2021-11-26      NaN  26259931    9  ...   
22      NaN      NaN  2021-11-26      NaN  27954591   45  ...   
23      NaN      NaN  2021-11-26      NaN  20982231   13  ...   
24      NaN      NaN  2021-11-26      NaN  27954592   46  ...   
27      NaN      NaN  2021-12-11      NaN  24357968    2  ...   
28      NaN      NaN  2021-12-11      NaN  28802292   29  ...   
29      NaN      NaN  2021-12-14      NaN  15598393   38  ...   
30      NaN      NaN  2021-12-15      NaN    359377   31  ...   
31      NaN      NaN  2021-12-17      NaN  29037956   44  ...   
32      NaN      NaN  2021-12-17      NaN  11730013   30  ...   
33      NaN      NaN  2021-12-17      NaN  29037983   19  ...   
36      NaN      NaN  2021-12-28      NaN   6125300   35  ...   
38      NaN      NaN  2022-01-17      NaN   6728756   23  ...   
39      NaN      NaN  2022-01-18      NaN  31607095    3  ...   
40      NaN      NaN  2022-01-18      NaN  31607101   51  ...   
41      NaN      NaN  2022-01-18      NaN  12455800   48  ...   
42      NaN      NaN  2022-01-18      NaN  14793782   47  ...   
43      NaN      NaN  2022-01-19      NaN   5223635   46  ...   
44      NaN      NaN  2022-01-20      NaN  20871667   49  ...   
73      NaN      NaN  2022-01-27      NaN  30899340   10  ...   
75      NaN      NaN  2022-01-27      NaN   9457496   34  ...   
76      NaN      NaN  2022-01-27      NaN  32147130   39  ...   
78      NaN      NaN  2022-01-30      NaN   6535233   43  ...   

   Additional.host.information    Lineage Clade  \
1                          NaN    AY.25.1    GK   
10                         NaN      AY.44    GK   
21                         NaN      AY.44    GK   
22                         N

In [47]:
data_dane['WEDSS_DOC'] = pd.to_datetime(data_dane['WEDSS_DOC'])
data_dane = data_dane.sort_values(by='WEDSS_DOC')


/var/folders/jt/pw4h3n2n3rz8mxjkqn3d57x00000gr/T/ipykernel_37068/1182996488.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [48]:
# Group by 'date' and calculate the cumulative percentage of True values, where there is 1 vax dose
grouped_df = data_dane.groupby('WEDSS_DOC')['1dose_or_more'].agg(['sum', 'count'])
grouped_df['Vax_Rate_1dose'] = (grouped_df['sum'].cumsum() / grouped_df['count'].cumsum())*100

# Reset the index for a cleaner dataframe
grouped_df = grouped_df.reset_index()

# Display the resulting grouped dataframe
print(grouped_df)



     WEDSS_DOC  sum  count  Vax_Rate_1dose
0   2021-02-23    0      1        0.000000
1   2021-02-24    0      3        0.000000
2   2021-02-25    0     13        0.000000
3   2021-02-26    0     10        0.000000
4   2021-02-27    0     16        0.000000
..         ...  ...    ...             ...
584 2023-05-09    0      1       47.994246
585 2023-05-10    1      3       47.987220
586 2023-05-14    0      1       47.979556
587 2023-05-20    0      1       47.971894
588 2023-05-30    0      1       47.964234

[589 rows x 4 columns]


In [49]:
grouped_df['WEDSS_DOC'] = pd.to_datetime(grouped_df['WEDSS_DOC'])

fig = px.line(grouped_df, x='WEDSS_DOC', y='Vax_Rate_1dose',
              title='Vaccination Rate in Dane County, 1+ dose')

fig.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig.show()

In [50]:
#repeat for MKE county
data_mke = data2[data2['CountyFIPS'] == 55079]


In [52]:
data_mke['WEDSS_DOC'] = pd.to_datetime(data_mke['WEDSS_DOC'])
data_mke = data_mke.sort_values(by='WEDSS_DOC')


In [21]:
# Group by 'date' and calculate the cumulative percentage of True values, where there is 1 vax dose
grouped_df2 = data_mke.groupby('WEDSS_DOC')['1dose_or_more'].agg(['sum', 'count'])
grouped_df2['Vax_Rate_1dose'] = (grouped_df2['sum'].cumsum() / grouped_df2['count'].cumsum())*100

# Reset the index for a cleaner dataframe
grouped_df2 = grouped_df2.reset_index()

# Display the resulting grouped dataframe
print(grouped_df2)


     WEDSS_DOC  sum  count  Vax_Rate_1dose
0   2020-03-12    0      1        0.000000
1   2020-03-14    0      1        0.000000
2   2020-03-15    0      7        0.000000
3   2020-03-17    0      3        0.000000
4   2020-03-18    0      1        0.000000
..         ...  ...    ...             ...
544 2023-04-10    0      1       33.700292
545 2023-04-13    0      1       33.692722
546 2023-05-03    0      1       33.685156
547 2023-05-04    1      1       33.700045
548 2023-06-15    0      1       33.692480

[549 rows x 4 columns]


In [53]:
grouped_df2['WEDSS_DOC'] = pd.to_datetime(grouped_df2['WEDSS_DOC'])

fig2 = px.line(grouped_df2, x='WEDSS_DOC', y='Vax_Rate_1dose',
              title='Vaccination Rate in Milwaukee County, 1+ dose')

#fig.add_trace(go.Scatter(x = grouped_df['WEDSS_DOC'], y = grouped_df['cumulative_percentage'], name = 'MKE'))


fig2.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig2.show()

In [54]:
wi_vax = pd.read_csv('WI_covid_vax_stats.tsv', sep ='\t')
wi_vax['Date'] = pd.to_datetime(wi_vax['Date']).dt.strftime('%Y-%m-%d')
wi_vax

Date   FIPS  MMWR_week     Recip_County Recip_State  \
0      2023-05-10  55129         19  Washburn County          WI   
1      2023-05-10  55073         19  Marathon County          WI   
2      2023-05-10  55031         19   Douglas County          WI   
3      2023-05-10  55069         19   Lincoln County          WI   
4      2023-05-10  55005         19    Barron County          WI   
...           ...    ...        ...              ...         ...   
43647  2020-12-13  55009         51     Brown County          WI   
43648  2020-12-13  55025         51      Dane County          WI   
43649  2020-12-13  55059         51   Kenosha County          WI   
43650  2020-12-13  55107         51      Rusk County          WI   
43651  2020-12-13  55017         51  Chippewa County          WI   

       Completeness_pct  Administered_Dose1_Recip  Administered_Dose1_Pop_Pct  \
0                  96.7                     11123                        70.8   
1                  96.7                     92033                        67.8   
2                  96.7                     26394                        61.2   
3                  96.7                     16612                        60.2   
4                  96.7                     26839                        59.3   
...                 ...                       ...                         ...   
43647               0.0                         0                         0.0   
43648               0.0                         0                         0.0   
43649               0.0                         0                         0.0   
43650               0.0                         0                         0.0   
43651               0.0                         0                         0.0   

       Administered_Dose1_Recip_5Plus  Administered_Dose1_Recip_5PlusPop_Pct  \
0                             11097.0                                   73.9   
1                             91409.0                                   71.5   
2                             26250.0                                   63.9   
3                             16569.0                                   63.0   
4                             26716.0                                   62.4   
...                               ...                                    ...   
43647                             NaN                                    NaN   
43648                             NaN                                    NaN   
43649                             NaN                                    NaN   
43650                             NaN                                    NaN   
43651                             NaN                                    NaN   

       ...  Census2019_18PlusPop  Census2019_65PlusPop  \
0      ...               12758.0                4304.0   
1      ...              104968.0               24682.0   
2      ...               34706.0                8288.0   
3      ...               22571.0                6118.0   
4      ...               35535.0               10213.0   
...    ...                   ...                   ...   
43647  ...              202324.0                   NaN   
43648  ...              436427.0                   NaN   
43649  ...              131558.0                   NaN   
43650  ...               11295.0                   NaN   
43651  ...               50522.0                   NaN   

       Bivalent_Booster_5Plus  Bivalent_Booster_5Plus_Pop_Pct  \
0                      3978.0                            26.5   
1                     23771.0                            18.6   
2                      8693.0                            21.2   
3                      5037.0                            19.1   
4                      8797.0                            20.6   
...                       ...                             ...   
43647                     NaN                             NaN   
43648                     NaN                

In [55]:
dane_vax = wi_vax.loc[wi_vax['FIPS'] == '55025']
dane_vax = dane_vax.rename(columns={'Administered_Dose1_Pop_Pct': 'Vax_Rate_1dose'})
dane_vax

Date   FIPS  MMWR_week Recip_County Recip_State  \
14     2023-05-10  55025         19  Dane County          WI   
83     2023-05-03  55025         18  Dane County          WI   
185    2023-04-26  55025         17  Dane County          WI   
252    2023-04-19  55025         16  Dane County          WI   
325    2023-04-12  55025         15  Dane County          WI   
...           ...    ...        ...          ...         ...   
43314  2020-12-17  55025         51  Dane County          WI   
43371  2020-12-16  55025         51  Dane County          WI   
43478  2020-12-15  55025         51  Dane County          WI   
43525  2020-12-14  55025         51  Dane County          WI   
43648  2020-12-13  55025         51  Dane County          WI   

       Completeness_pct  Administered_Dose1_Recip  Vax_Rate_1dose  \
14                 96.7                    525490            95.0   
83                 96.7                    525321            95.0   
185                96.7                    525182            95.0   
252                96.7                    525029            95.0   
325                96.7                    524856            95.0   
...                 ...                       ...             ...   
43314               0.0                         0             0.0   
43371               0.0                         0             0.0   
43478               0.0                         0             0.0   
43525               0.0                         0             0.0   
43648               0.0                         0             0.0   

       Administered_Dose1_Recip_5Plus  Administered_Dose1_Recip_5PlusPop_Pct  \
14                           513813.0                                   95.0   
83                           513685.0                                   95.0   
185                          513569.0                                   95.0   
252                          513471.0                                   95.0   
325                          513370.0                                   95.0   
...                               ...                                    ...   
43314                             NaN                                    NaN   
43371                             NaN                                    NaN   
43478                             NaN                                    NaN   
43525                             NaN                                    NaN   
43648                             NaN                                    NaN   

       ...  Census2019_18PlusPop  Census2019_65PlusPop  \
14     ...              436427.0               77771.0   
83     ...              436427.0               77771.0   
185    ...              436427.0               77771.0   
252    ...              436427.0               77771.0   
325    ...              436427.0               77771.0   
...    ...                   ...                   ...   
43314  ...              436427.0                   NaN   
43371  ...              436427.0                   NaN   
43478  ...              436427.0                   NaN   
43525  ...              436427.0                   NaN   
43648  ...              436427.0                   NaN   

       Bivalent_Booster_5Plus  Bivalent_Booster_5Plus_Pop_Pct  \
14                   225692.0                            43.7   
83                   223585.0                            43.3   
185                  221690.0                            42.9   
252                  220772.0                            42.7   
325                  220498.0                            42.7   
...                       ...                             ...   
43314                     NaN                             NaN   
43371                     NaN                             NaN   
43478                     NaN                             NaN   
43525                     NaN                             NaN   
43648                     NaN             

In [56]:
mke_vax = wi_vax.loc[wi_vax['FIPS'] == '55079']
mke_vax = mke_vax.rename(columns={'Administered_Dose1_Pop_Pct': 'Vax_Rate_1dose'})
mke_vax

Date   FIPS  MMWR_week      Recip_County Recip_State  \
60     2023-05-10  55079         19  Milwaukee County          WI   
98     2023-05-03  55079         18  Milwaukee County          WI   
211    2023-04-26  55079         17  Milwaukee County          WI   
268    2023-04-19  55079         16  Milwaukee County          WI   
300    2023-04-12  55079         15  Milwaukee County          WI   
...           ...    ...        ...               ...         ...   
43358  2020-12-17  55079         51  Milwaukee County          WI   
43395  2020-12-16  55079         51  Milwaukee County          WI   
43471  2020-12-15  55079         51  Milwaukee County          WI   
43533  2020-12-14  55079         51  Milwaukee County          WI   
43605  2020-12-13  55079         51  Milwaukee County          WI   

       Completeness_pct  Administered_Dose1_Recip  Vax_Rate_1dose  \
60                 96.7                    720210            76.2   
98                 96.7                    719972            76.1   
211                96.7                    719806            76.1   
268                96.7                    719605            76.1   
300                96.7                    719420            76.1   
...                 ...                       ...             ...   
43358               0.0                         0             0.0   
43395               0.0                         0             0.0   
43471               0.0                         0             0.0   
43533               0.0                         0             0.0   
43605               0.0                         0             0.0   

       Administered_Dose1_Recip_5Plus  Administered_Dose1_Recip_5PlusPop_Pct  \
60                           711060.0                                   80.7   
98                           710844.0                                   80.6   
211                          710691.0                                   80.6   
268                          710518.0                                   80.6   
300                          710383.0                                   80.6   
...                               ...                                    ...   
43358                             NaN                                    NaN   
43395                             NaN                                    NaN   
43471                             NaN                                    NaN   
43533                             NaN                                    NaN   
43605                             NaN                                    NaN   

       ...  Census2019_18PlusPop  Census2019_65PlusPop  \
60     ...              720305.0              132290.0   
98     ...              720305.0              132290.0   
211    ...              720305.0              132290.0   
268    ...              720305.0              132290.0   
300    ...              720305.0              132290.0   
...    ...                   ...                   ...   
43358  ...              720305.0                   NaN   
43395  ...              720305.0                   NaN   
43471  ...              720305.0                   NaN   
43533  ...              720305.0                   NaN   
43605  ...              720305.0                   NaN   

       Bivalent_Booster_5Plus  Bivalent_Booster_5Plus_Pop_Pct  \
60                   195040.0                            22.1   
98                   193544.0                            22.0   
211                  192099.0                            21.8   
268                  191136.0                            21.7   
300                  190986.0                            21.7   
...                       ...                             ...   
43358                     NaN                             NaN   
43395                     NaN                             NaN   
43471                     NaN                             NaN   
43533                     NaN                  

In [57]:

fig3 = px.line(dane_vax, x="Date", y='Vax_Rate_1dose',
              hover_data={"Date": "|%B %d, %Y"},
              title='Vaccination Rate in Dane County, 1+ dose')
fig3.update_xaxes(
    dtick="M1",
    tickformat="%b\n%Y")
fig3.show()

In [58]:
# Create traces for each dataframe
trace1 = go.Scatter(x=dane_vax['Date'], y=dane_vax['Vax_Rate_1dose'], mode='lines', name='vax_stats, Dane')
trace2 = go.Scatter(x=grouped_df['WEDSS_DOC'], y=grouped_df['Vax_Rate_1dose'], mode='lines', name='dataset, Dane')

# Create the layout for the plot
layout = go.Layout(title='Vaccination Rate in Dane County, 1+ dose',
                   xaxis=dict(title='Date'),
                   yaxis=dict(title='Percent Vaccinated (%)'))

# Combine traces into a list
fig_data = [trace1, trace2]

# Create the figure
fig_dane = go.Figure(data=fig_data, layout=layout)

# Show the figure
fig_dane.show()

fig_dane.write_html("data_summary_figs/2024-01-16_dane_vax_stats.html")


In [59]:
# Create traces for each dataframe
trace1 = go.Scatter(x=dane_vax['Date'], y=dane_vax['Vax_Rate_1dose'], mode='lines', name='vax_stats, Dane')
trace3 = go.Scatter(x=grouped_df['WEDSS_DOC'], y=grouped_df['Vax_Rate_1dose'], mode='lines', name='dataset, Dane')
trace4 = go.Scatter(x=grouped_df2['WEDSS_DOC'], y=grouped_df2['Vax_Rate_1dose'], mode= 'lines', name='dataset, MKE')
trace2 = go.Scatter(x=mke_vax['Date'], y=mke_vax['Vax_Rate_1dose'], mode= 'lines', name='vax_stats, MKE')


# Create the layout for the plot
layout = go.Layout(title='Vaccination Rate in Dane and Milwaukee County, 1+ dose',
                   xaxis=dict(title='Date'),
                   yaxis=dict(title='Percent Vaccinated (%)'))

# Combine traces into a list
fig_data2 = [trace1, trace2, trace3, trace4]

# Create the figure
fig_WI = go.Figure(data=fig_data2, layout=layout)

# Show the figure
fig_WI.show()

In [60]:
#seq count over time by county
fig4 = px.histogram(data2, x='WEDSS_DOC', nbins=43, title='Sequence data over time', color ='County')
fig4.update_xaxes(showgrid=True, ticklabelmode="period", dtick="M3", tickformat="%b\n%Y")

fig4.show()
fig4.write_html("data_summary_figs/2024-01-17_seqs_by_county.html")


In [61]:
#histogram of samples by # of vaccines, can isolate each count's data by double click on legend
fig5 = px.histogram(data2, x='WEDSS_DOC', nbins=43, title='Sequence data over time by vax status', color ='vax_count')
fig5.update_xaxes(showgrid=True, ticklabelmode="period", dtick="M3", tickformat="%b\n%Y")

fig5.show()

In [62]:
#histogram of samples over time 
fig6 = px.histogram(data2, x='WEDSS_DOC', nbins=43, title='Sequence data over time', color ='Gender.x')
fig6.update_xaxes(showgrid=True, ticklabelmode="period", dtick="M3", tickformat="%b\n%Y")

fig6.show()

In [63]:
#histogram of samples by # of vaccines, can isolate each count's data by double click on legend
fig6 = px.histogram(data2, x='WEDSS_DOC', nbins=50, title='Sequence data by clade', color ='Clade')
fig6.update_xaxes(showgrid=True, ticklabelmode="period", dtick="M3", tickformat="%b\n%Y")

fig6.show()